In [1]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objs as go
from plotly.subplots import make_subplots

## Data

In [77]:
data = pd.read_csv(r'./big_mart_sales/train_v9rqX0R.csv')
data.head()

Item_Identifier  Item_Weight Item_Fat_Content  Item_Visibility  \
0           FDA15         9.30          Low Fat         0.016047   
1           DRC01         5.92          Regular         0.019278   
2           FDN15        17.50          Low Fat         0.016760   
3           FDX07        19.20          Regular         0.000000   
4           NCD19         8.93          Low Fat         0.000000   

               Item_Type  Item_MRP Outlet_Identifier  \
0                  Dairy  249.8092            OUT049   
1            Soft Drinks   48.2692            OUT018   
2                   Meat  141.6180            OUT049   
3  Fruits and Vegetables  182.0950            OUT010   
4              Household   53.8614            OUT013   

   Outlet_Establishment_Year Outlet_Size Outlet_Location_Type  \
0                       1999      Medium               Tier 1   
1                       2009      Medium               Tier 3   
2                       1999      Medium               Tier 1   
3                       1998         NaN               Tier 3   
4                       1987        High               Tier 3   

         Outlet_Type  Item_Outlet_Sales  
0  Supermarket Type1          3735.1380  
1  Supermarket Type2           443.4228  
2  Supermarket Type1          2097.2700  
3      Grocery Store           732.3800  
4  Supermarket Type1           994.7052

### Data Preprocessing

In [78]:
# Data Preprocessing
rectify_Item_Fat_Content_typo = {'LF': 'Low Fat', 'low fat': 'Low Fat', 'Low Fat': 'Low Fat', 'reg': 'Regular', 'Regular': 'Regular'}
data['Item_Fat_Content'] = data['Item_Fat_Content'].map(rectify_Item_Fat_Content_typo)

### Variable Identification

In [3]:
num_cols = ['Item_Weight', 'Item_Visibility', 'Item_MRP', 'Item_Outlet_Sales']
cat_cols = ['Item_Identifier', 'Item_Fat_Content', 'Item_Type', 'Outlet_Identifier', 'Outlet_Size', 'Outlet_Location_Type', 'Outlet_Type']
ordinal_cols = ['Item_Fat_Content', 'Outlet_Size', 'Outlet_Location_Type']
target_var = ['Item_Outlet_Sales']

## Univariate analysis

### Continuous Variables

In [4]:
for cols in num_cols:

    # Central tendency
    print(data[cols].describe())
    print(data[cols].skew())
    print(data[cols].kurtosis())
    
    # Subplots
    fig = make_subplots(rows=1, cols=3)
    
    # Hist plot     
    fig.add_trace(go.Histogram(x=data[cols],
                              name='Histogram'), row=1,col=1)
    
    # Box plot
    fig.add_trace(go.Box(y=data[cols],
                        boxpoints='all',
                        name='Box Plot'), row=1, col=2)
    
    # ECDF plot
    x = np.sort(data[cols])
    n = len(data[cols])
    y = np.arange(1, n+1)/n
    fig.add_trace(go.Scatter(x=x, 
                             y=y,
                            name='ECDF'), row=1, col=3)
    
    # Layout update
    fig.update_layout(bargap=0.03,
                  title=dict(text='Distribution of {}'.format(cols)),
                margin=dict(l=80, r=80, t=100, b=80))
    
    fig.show()

count    7060.000000
mean       12.857645
std         4.643456
min         4.555000
25%         8.773750
50%        12.600000
75%        16.850000
max        21.350000
Name: Item_Weight, dtype: float64
0.0824262091221237
-1.2277664144376634


count    8523.000000
mean        0.066132
std         0.051598
min         0.000000
25%         0.026989
50%         0.053931
75%         0.094585
max         0.328391
Name: Item_Visibility, dtype: float64
1.1670905496918407
1.6794454826024245


count    8523.000000
mean      140.992782
std        62.275067
min        31.290000
25%        93.826500
50%       143.012800
75%       185.643700
max       266.888400
Name: Item_MRP, dtype: float64
0.1272022683110526
-0.8897690936963571


count     8523.000000
mean      2181.288914
std       1706.499616
min         33.290000
25%        834.247400
50%       1794.331000
75%       3101.296400
max      13086.964800
Name: Item_Outlet_Sales, dtype: float64
1.1775306028542798
1.6158766814287264


### Continuous - Continuous

In [5]:
data[num_cols].corr()

Item_Weight  Item_Visibility  Item_MRP  Item_Outlet_Sales
Item_Weight           1.000000        -0.014048  0.027141           0.014123
Item_Visibility      -0.014048         1.000000 -0.001315          -0.128625
Item_MRP              0.027141        -0.001315  1.000000           0.567574
Item_Outlet_Sales     0.014123        -0.128625  0.567574           1.000000

### Categorical Variables

In [73]:
for col in cat_cols:
    # Find the count and count percentage of the column
    col_count = data[col].value_counts(dropna=False)
    col_count_perc = data[col].value_counts(dropna=False)/len(data[col])* 100
    
    #Subplots
    fig=make_subplots(rows=1, cols=2)

    # Count bar graph
    fig.add_trace(go.Bar(x=col_count.index,
                         y=col_count,
                         name="Count",
                        text=col_count),
                  row=1, col=1)
    
    # Count percentage bar graph
    fig.add_trace(go.Bar(x=col_count_perc.index,
                         y=col_count_perc,
                         name="Count (%)",
                        text=col_count_perc,
                         texttemplate='%{text:.2s}%'),
                  row=1, col=2)

    # Layout update
    fig.update_layout(title=dict(text='Categories count and count% of column {}'.format(col)),
                      margin=dict(l=80, r=80, t=100, b=80))
    fig.update_traces(textposition='outside')
    fig.update_yaxes(showticklabels=False)

    fig.show()

### Categorical - Categorical

In [7]:
cat_cols

['Item_Identifier',
 'Item_Fat_Content',
 'Item_Type',
 'Outlet_Identifier',
 'Outlet_Size',
 'Outlet_Location_Type',
 'Outlet_Type']

In [100]:
from scipy.stats import chi2_contingency

In [101]:
def get_chi_stats(df, nominal_col1, nominal_col2):
    """
    Do Chi sqaured test of independence
    df: input data
    nominal_col1: Name of the nominal/categorical col in df
    nominal_col2: Name of the nominal/categorical col in df
    """
    if not df.empty:
        observed = pd.crosstab(index=df[nominal_col1],
                               columns=df[nominal_col2],
                               margins=True,
                               margins_name='Total')
        chi2_value, p_value, degree_of_freedom, expected = chi2_contingency(observed, correction=False)
        print("Chi Statistics", chi2_value,
              "\nProbability value", p_value,
              "\nDegree of freedom", degree_of_freedom)

In [102]:
get_chi_stats(data, 'Item_Fat_Content', 'Item_Type')

Chi Statistics 1509.0010155480727 
Probability value 2.4082163223141427e-297 
Degree of freedom 32


In [99]:
# Form two-way count table
two_way_table = pd.crosstab(index=data['Item_Fat_Content'],
                            columns=data['Item_Type'],
                            margins=False,
                            dropna=False) \
    .reset_index()

# 2 way frequency table
two_way_table_frequency = pd.crosstab(index=data['Item_Fat_Content'],
                                      columns=data['Item_Type'],
                                      margins=False,
                                      dropna=False) \
    .apply(lambda r: (r / r.sum()) * 100, axis=1) \
    .reset_index()

# For plotting stack bar count
df_stacked_bar = two_way_table.melt(id_vars=["Item_Fat_Content"],
                                    var_name="Item_Type",
                                    value_name="two_way_count")

# For plotting stack bar percent
df_stacked_bar_perc = two_way_table_frequency.melt(id_vars=["Item_Fat_Content"],
                                                   var_name="Item_Type",
                                                   value_name="two_way_count")

fig = px.bar(df_stacked_bar_perc.sort_values(['Item_Fat_Content', 'two_way_count'], ascending=False),
             x='Item_Type',
             y='two_way_count',
             color='Item_Fat_Content')

fig.show()

### Catergorical - Continuous

In [104]:
cat_cols, target_var

(['Item_Identifier',
  'Item_Fat_Content',
  'Item_Type',
  'Outlet_Identifier',
  'Outlet_Size',
  'Outlet_Location_Type',
  'Outlet_Type'],
 ['Item_Outlet_Sales'])

In [110]:
# Plot
fig = go.Figure(go.Box(x=data['Item_Fat_Content'],
                       y=data['Item_Outlet_Sales']))
fig.show()

### Treat missing values

In [16]:
data.isnull().sum()

Item_Identifier                 0
Item_Fat_Content                0
Item_Visibility                 0
Item_Type                       0
Item_MRP                        0
Outlet_Identifier               0
Outlet_Establishment_Year       0
Outlet_Size                  2410
Outlet_Location_Type            0
Outlet_Type                     0
Item_Outlet_Sales               0
Item_Weight                     0
dtype: int64

In [15]:
# Get unique weight of each product
unique_item_weight = data[~data['Item_Weight'].isnull()][['Item_Identifier', 'Item_Weight']].drop_duplicates()

# ASsign the unique weight obtained to the respective product 
data.drop(['Item_Weight'], axis=1, inplace=True)
data = pd.merge(data, unique_item_weight, on='Item_Identifier', how='left')

# Pending missing value
data = data[~data.Item_Weight.isnull()]

In [9]:
# Get unique size of each outlet
unique_outlet_size = data[~data['Outlet_Size'].isnull()][['Outlet_Identifier', 'Outlet_Size']].drop_duplicates()

# ASsign the unique weight obtained to the respective product 
data.drop(['Outlet_Size'], axis=1, inplace=True)
data = pd.merge(data, unique_outlet_size, on='Outlet_Identifier', how='left')

# Pending missing value
data[data.Outlet_Size.isnull()]

Item_Identifier Item_Fat_Content  Item_Visibility              Item_Type  \
3              FDX07          Regular         0.000000  Fruits and Vegetables   
8              FDH17          Regular         0.016687           Frozen Foods   
9              FDU28          Regular         0.094450           Frozen Foods   
25             NCD06          Low Fat         0.099887              Household   
28             FDE51          Regular         0.161467                  Dairy   
30             FDV38          Low Fat         0.170349                  Dairy   
33             FDO23          Low Fat         0.000000                 Breads   
45             FDM39               LF         0.089499                  Dairy   
46             NCP05          Low Fat         0.000000     Health and Hygiene   
47             FDV49          Low Fat         0.025880                 Canned   
53             FDA43          Low Fat         0.065042  Fruits and Vegetables   
54             NCP18          Low Fat         0.028760              Household   
56             NCX54          Low Fat         0.048157              Household   
61             FDV27          Regular         0.040071                   Meat   
65             FDC46               LF         0.195068            Snack Foods   
67             FDZ03          Regular         0.078946                  Dairy   
68             DRH37          Low Fat         0.041701            Soft Drinks   
72             FDH35          Low Fat         0.000000          Starchy Foods   
73             FDG02          Low Fat         0.011325                 Canned   
78             FDL04          Low Fat         0.112557           Frozen Foods   
79             FDV25          Low Fat         0.000000                 Canned   
85             FDG20          Regular         0.126399  Fruits and Vegetables   
90             FDW20          Low Fat         0.040421  Fruits and Vegetables   
92             DRI25          Low Fat         0.033970            Soft Drinks   
100            FDT28          Low Fat         0.063695           Frozen Foods   
107            FDG12          Regular         0.000000           Baking Goods   
111            FDS52          low fat         0.005505           Frozen Foods   
114            FDV11          Regular         0.000000                 Breads   
116            FDZ16          Regular         0.160760           Frozen Foods   
118            DRA12          Low Fat         0.041178            Soft Drinks   
...              ...              ...              ...                    ...   
8413           NCU05          Low Fat         0.058855     Health and Hygiene   
8427           FDA44          Low Fat         0.053331  Fruits and Vegetables   
8428           FDI16          Regular         0.227261           Frozen Foods   
8442           FDT04          Low Fat         0.107259           Frozen Foods   
8443           FDS26          Low Fat         0.089975                  Dairy   
8448           NCO42          Low Fat         0.024795              Household   
8449           FDB46          Regular         0.093954            Snack Foods   
8451           FDL26          Low Fat         0.073607                 Canned   
8452           NCQ30          Low Fat         0.029131              Household   
8460           FDO56          Regular         0.045074  Fruits and Vegetables   
8461           FDX11          Regular         0.106969           Baking Goods   
8464           FDB20          Low Fat         0.052086  Fruits and Vegetables   
8467           NCT53          Low Fat         0.048388     Health and Hygiene   
8469           DRI47          Low Fat         0.035016            Hard Drinks   
8470           NCJ42          Low Fat         0.014330              Household   
8472           NCO41          Low Fat         0.018887     Health and Hygiene   
8473           FDC05          Regular         0.099343           Frozen Foods   
8477           FDT56          Regula

In [10]:
data.groupby(['Outlet_Identifier']).agg({'Outlet_Type':'nunique'})

Outlet_Type
Outlet_Identifier             
OUT010                       1
OUT013                       1
OUT017                       1
OUT018                       1
OUT019                       1
OUT027                       1
OUT035                       1
OUT045                       1
OUT046                       1
OUT049                       1

In [11]:
unique_outlet_size

Outlet_Identifier Outlet_Size
0             OUT049      Medium
1             OUT018      Medium
4             OUT013        High
7             OUT027      Medium
11            OUT046       Small
19            OUT035       Small
23            OUT019       Small